In [ ]:
import numpy as np
import pandas as pd
import os
import matplotlib.pyplot as plt

# 가스 농도 계산 함수 (Farrell’s Concentration Equation 적용)
def calculate_gas_concentration(filament_pos, sigma, num_moles, grid_x, grid_y, grid_z):
    distance = np.sqrt((grid_x - filament_pos[0]) ** 2 + (grid_y - filament_pos[1]) ** 2 + (grid_z - filament_pos[2]) ** 2)
    concentration = (num_moles / (np.sqrt(8 * np.pi**3) * sigma**3)) * np.exp(-distance**2 / (2 * sigma**2))
    return concentration

# 시각화 함수 정의
def visualize_gas_concentration_2d_3d(grid_x, grid_y, grid_z, gas_concentration, slice_index, save_dir):
    # 2D 시각화
    plt.figure(figsize=(10, 6))
    levels = np.linspace(np.min(gas_concentration[:, :, slice_index]), 
                         np.max(gas_concentration[:, :, slice_index]), 300)
    contour = plt.contourf(grid_x[:, :, slice_index], grid_y[:, :, slice_index], 
                           gas_concentration[:, :, slice_index], levels=levels, cmap='viridis')
    plt.colorbar(contour)
    plt.title('Gas Concentration Map (2D)')
    plt.savefig(f'{save_dir}/gas_concentration_2d.png')  # 2D 이미지 저장
    plt.show()

    # 3D 시각화
    fig = plt.figure(figsize=(10, 8))
    ax = fig.add_subplot(111, projection='3d')
    ax.scatter(grid_x.flatten(), grid_y.flatten(), grid_z.flatten(), 
               c=gas_concentration.flatten(), cmap='viridis', marker='o')
    ax.set_xlabel('X Position (m)')
    ax.set_ylabel('Y Position (m)')
    ax.set_zlabel('Z Position (m)')
    plt.title('Gas Concentration Map (3D)')
    plt.savefig(f'{save_dir}/gas_concentration_3d.png')  # 3D 이미지 저장
    plt.show()

# 기본 경로 설정 
base_dir = '/home/piai/PABA/gaden/install/test_env/share/test_env/scenarios/2_suc_map/'
map_num = 'map06'  # 사용자가 정의할 맵 번호

# 시뮬레이션 폴더 반복 처리
for sim_index in range(1, 21):  # sim1부터 sim20까지의 시뮬레이션 폴더 확인
    sim_num = f'sim{sim_index}'
    sim_dir = f'{base_dir}/{map_num}/gas_simulations/{sim_num}'  # 원래 위치에서 CSV 파일을 읽기 위한 경로
    
    # 해당 시뮬레이션 디렉토리가 존재하는지 확인
    if os.path.exists(sim_dir):
        print(f"Processing {sim_dir}")
        
        csv_path = f'{sim_dir}/iteration_300.csv'
        
        if os.path.exists(csv_path):
            # CSV 파일 로드
            meta_data_keys = pd.read_csv(csv_path, nrows=1)
            meta_data_values = pd.read_csv(csv_path, nrows=1)

            column_names = pd.read_csv(csv_path, skiprows=2, nrows=1, header=None).values[0].tolist()
            data = pd.read_csv(csv_path, skiprows=3, names=column_names)

            # 메타데이터 딕셔너리로 변환
            meta_data = dict(zip(meta_data_keys.columns, meta_data_values.values[0]))

            # 필요한 데이터 추출 (필라멘트 위치, Sigma 값, Num Moles 값)
            positions = data[['Position X', 'Position Y', 'Position Z']].values
            sigma_values = data['Sigma'].values
            num_moles = meta_data['Num Moles All Gases in cm3']
            filament_moles = meta_data['Filament Moles']

            print(f"Positions: {positions}")
            print(f"Sigma Values: {sigma_values}")
            print(f"Num Moles All Gases in cm3: {num_moles}")
            print(f"Filament Moles: {filament_moles}")

            # 환경 설정 (Grid 정의)
            env_min = np.array([-0.2, -0.2, 0])
            env_max = np.array([10.2, 6.2, 2.5])
            num_cells = np.array([104, 64, 25])
            x = np.linspace(env_min[0], env_max[0], num_cells[0])
            y = np.linspace(env_min[1], env_max[1], num_cells[1])
            z = np.linspace(env_min[2], env_max[2], num_cells[2])
            grid_x, grid_y, grid_z = np.meshgrid(x, y, z, indexing='ij')
            grid_shape = grid_x.shape

            # 가스 농도 초기화
            gas_concentration = np.zeros(grid_shape)

            # 각 필라멘트에 대해 농도 계산 및 누적
            for i in range(len(positions)):
                filament_pos = positions[i]
                sigma = sigma_values[i]
                num_moles_gas = num_moles  # 메타데이터에서 가져온 값
                concentration = calculate_gas_concentration(filament_pos, sigma, num_moles_gas, grid_x, grid_y, grid_z)
                gas_concentration += concentration  # 누적

            # Z축 중간 슬라이스 선택
            slice_index = grid_shape[2] // 2

            # 저장 경로 설정 
            save_dir = f'{base_dir}/{map_num}/feature_map/{sim_num}'  
            os.makedirs(save_dir, exist_ok=True)

            # 2D 및 3D 시각화 및 저장
            visualize_gas_concentration_2d_3d(grid_x, grid_y, grid_z, gas_concentration, slice_index, save_dir)

            # 2D 배열을 넘파이로 저장
            np.save(f'{save_dir}/gas_concentration_map.npy', gas_concentration[:, :, slice_index])

            print(f"Gas concentration maps (2D & 3D) and .npy file have been saved to {save_dir}")
        else:
            print(f"No CSV file found for {sim_dir}")
    else:
        print(f"Skipping non-existent directory {sim_dir}")

In [ ]:
import numpy as np
import pandas as pd
import os
import matplotlib.pyplot as plt

# 가스 농도 계산 함수 (Farrell’s Concentration Equation 적용)
def calculate_gas_concentration(filament_pos, sigma, num_moles, grid_x, grid_y, grid_z):
    distance = np.sqrt((grid_x - filament_pos[0]) ** 2 + (grid_y - filament_pos[1]) ** 2 + (grid_z - filament_pos[2]) ** 2)
    concentration = (num_moles / (np.sqrt(8 * np.pi**3) * sigma**3)) * np.exp(-distance**2 / (2 * sigma**2))
    return concentration

# 시각화 함수 정의
def visualize_gas_concentration_2d_3d(grid_x, grid_y, grid_z, gas_concentration, slice_index, save_dir):
    # 2D 시각화
    plt.figure(figsize=(10, 6))
    levels = np.linspace(np.min(gas_concentration[:, :, slice_index]), 
                         np.max(gas_concentration[:, :, slice_index]), 300)
    contour = plt.contourf(grid_x[:, :, slice_index], grid_y[:, :, slice_index], 
                           gas_concentration[:, :, slice_index], levels=levels, cmap='viridis')
    plt.colorbar(contour)
    plt.title('Gas Concentration Map (2D)')
    plt.savefig(f'{save_dir}/gas_concentration_2d.png')  # 2D 이미지 저장
    plt.show()

    # 3D 시각화
    fig = plt.figure(figsize=(10, 8))
    ax = fig.add_subplot(111, projection='3d')
    ax.scatter(grid_x.flatten(), grid_y.flatten(), grid_z.flatten(), 
               c=gas_concentration.flatten(), cmap='viridis', marker='o')
    ax.set_xlabel('X Position (m)')
    ax.set_ylabel('Y Position (m)')
    ax.set_zlabel('Z Position (m)')
    plt.title('Gas Concentration Map (3D)')
    plt.savefig(f'{save_dir}/gas_concentration_3d.png')  # 3D 이미지 저장
    plt.show()

# 기본 경로 설정 
base_dir = '/home/piai/PABA/gaden/install/test_env/share/test_env/scenarios/2_suc_map/'

# map 폴더 자동 검색
map_dirs = [d for d in os.listdir(base_dir) if os.path.isdir(os.path.join(base_dir, d)) and d.startswith('map')]

# 시뮬레이션 폴더 반복 처리
for map_num in map_dirs:
    print(f"Processing {map_num}")
    for sim_index in range(1, 21):  # sim1부터 sim20까지의 시뮬레이션 폴더 확인
        sim_num = f'sim{sim_index}'
        sim_dir = f'{base_dir}/{map_num}/gas_simulations/{sim_num}'  # 원래 위치에서 CSV 파일을 읽기 위한 경로
        
        # 해당 시뮬레이션 디렉토리가 존재하는지 확인
        if os.path.exists(sim_dir):
            print(f"Processing {sim_dir}")
            
            csv_path = f'{sim_dir}/iteration_300.csv'
            
            if os.path.exists(csv_path):
                # CSV 파일 로드
                meta_data_keys = pd.read_csv(csv_path, nrows=1)
                meta_data_values = pd.read_csv(csv_path, nrows=1)

                column_names = pd.read_csv(csv_path, skiprows=2, nrows=1, header=None).values[0].tolist()
                data = pd.read_csv(csv_path, skiprows=3, names=column_names)

                # 메타데이터 딕셔너리로 변환
                meta_data = dict(zip(meta_data_keys.columns, meta_data_values.values[0]))

                # 필요한 데이터 추출 (필라멘트 위치, Sigma 값, Num Moles 값)
                positions = data[['Position X', 'Position Y', 'Position Z']].values
                sigma_values = data['Sigma'].values
                num_moles = meta_data['Num Moles All Gases in cm3']
                filament_moles = meta_data['Filament Moles']

                print(f"Positions: {positions}")
                print(f"Sigma Values: {sigma_values}")
                print(f"Num Moles All Gases in cm3: {num_moles}")
                print(f"Filament Moles: {filament_moles}")

                # 환경 설정 (Grid 정의)
                env_min = np.array([-0.2, -0.2, 0])
                env_max = np.array([10.2, 6.2, 2.5])
                num_cells = np.array([104, 64, 25])
                x = np.linspace(env_min[0], env_max[0], num_cells[0])
                y = np.linspace(env_min[1], env_max[1], num_cells[1])
                z = np.linspace(env_min[2], env_max[2], num_cells[2])
                grid_x, grid_y, grid_z = np.meshgrid(x, y, z, indexing='ij')
                grid_shape = grid_x.shape

                # 가스 농도 초기화
                gas_concentration = np.zeros(grid_shape)

                # 각 필라멘트에 대해 농도 계산 및 누적
                for i in range(len(positions)):
                    filament_pos = positions[i]
                    sigma = sigma_values[i]
                    num_moles_gas = num_moles  # 메타데이터에서 가져온 값
                    concentration = calculate_gas_concentration(filament_pos, sigma, num_moles_gas, grid_x, grid_y, grid_z)
                    gas_concentration += concentration  # 누적

                # Z축 중간 슬라이스 선택
                slice_index = grid_shape[2] // 2

                # 저장 경로 설정 
                save_dir = f'{base_dir}/{map_num}/feature_map/{sim_num}'  
                os.makedirs(save_dir, exist_ok=True)

                # 2D 및 3D 시각화 및 저장
                visualize_gas_concentration_2d_3d(grid_x, grid_y, grid_z, gas_concentration, slice_index, save_dir)

                # 2D 배열을 넘파이로 저장
                np.save(f'{save_dir}/gas_concentration_map.npy', gas_concentration[:, :, slice_index])

                print(f"Gas concentration maps (2D & 3D) and .npy file have been saved to {save_dir}")
            else:
                print(f"No CSV file found for {sim_dir}")
        else:
            print(f"Skipping non-existent directory {sim_dir}")

In [ ]:
def calculate_average_concentration(sim_dir, iterations, grid_shape):
    gas_concentration_total = np.zeros(grid_shape)
    count = 0

    for iteration in iterations:
        csv_path = f'{sim_dir}/iteration_{iteration}.csv'
        if os.path.exists(csv_path):
            # CSV 파일 로드 및 concentration 계산 (이전 코드와 동일)
            concentration = calculate_gas_concentration(filament_pos, sigma, num_moles_gas, grid_x, grid_y, grid_z)
            gas_concentration_total += concentration
            count += 1
        else:
            print(f"Skipping non-existent iteration {iteration}")
    
    if count > 0:
        return gas_concentration_total / count  # 평균 농도 지도
    else:
        return None

# 평균 농도 지도를 생성할 iteration 범위 설정
iterations = range(290, 311)
average_concentration_map = calculate_average_concentration(sim_dir, iterations, grid_shape)
if average_concentration_map is not None:
    # 결과 저장
    np.save(f'{save_dir}/average_gas_concentration_map.npy', average_concentration_map)
    print("Average concentration map saved.")


In [ ]:
def save_individual_concentration_maps(sim_dir, iterations, grid_shape, save_dir):
    for iteration in iterations:
        csv_path = f'{sim_dir}/iteration_{iteration}.csv'
        if os.path.exists(csv_path):
            # CSV 파일 로드 및 concentration 계산 (이전 코드와 동일)
            concentration = calculate_gas_concentration(filament_pos, sigma, num_moles_gas, grid_x, grid_y, grid_z)
            
            # 결과 저장
            np.save(f'{save_dir}/gas_concentration_map_{iteration}.npy', concentration)
            print(f"Concentration map for iteration {iteration} saved.")
        else:
            print(f"Skipping non-existent iteration {iteration}")

# 여러 농도 지도를 생성할 iteration 범위 설정
iterations = [298, 299, 300, 301, 302]
save_individual_concentration_maps(sim_dir, iterations, grid_shape, save_dir)


In [ ]:
import numpy as np
import pandas as pd
import os
import matplotlib.pyplot as plt

# 가스 농도 계산 함수 (Farrell’s Concentration Equation 적용)
def calculate_gas_concentration(filament_pos, sigma, num_moles, grid_x, grid_y, grid_z):
    distance = np.sqrt((grid_x - filament_pos[0]) ** 2 + (grid_y - filament_pos[1]) ** 2 + (grid_z - filament_pos[2]) ** 2)
    concentration = (num_moles / (np.sqrt(8 * np.pi**3) * sigma**3)) * np.exp(-distance**2 / (2 * sigma**2))
    return concentration

# 시각화 함수 정의
def visualize_gas_concentration_2d_3d(grid_x, grid_y, grid_z, gas_concentration, slice_index, save_dir):
    # 2D 시각화
    plt.figure(figsize=(10, 6))
    levels = np.linspace(np.min(gas_concentration[:, :, slice_index]), 
                         np.max(gas_concentration[:, :, slice_index]), 300)
    contour = plt.contourf(grid_x[:, :, slice_index], grid_y[:, :, slice_index], 
                           gas_concentration[:, :, slice_index], levels=levels, cmap='viridis')
    plt.colorbar(contour)
    plt.title('Gas Concentration Map (2D)')
    plt.savefig(f'{save_dir}/gas_concentration_2d.png')  # 2D 이미지 저장
    plt.show()

    # 3D 시각화
    fig = plt.figure(figsize=(10, 8))
    ax = fig.add_subplot(111, projection='3d')
    ax.scatter(grid_x.flatten(), grid_y.flatten(), grid_z.flatten(), 
               c=gas_concentration.flatten(), cmap='viridis', marker='o')
    ax.set_xlabel('X Position (m)')
    ax.set_ylabel('Y Position (m)')
    ax.set_zlabel('Z Position (m)')
    plt.title('Gas Concentration Map (3D)')
    plt.savefig(f'{save_dir}/gas_concentration_3d.png')  # 3D 이미지 저장
    plt.show()

# 경로 설정
base_dir = '/home/piai/PABA/gaden/install/test_env/share/test_env/scenarios/2_suc_map/'

# 모든 map 폴더와 sim 폴더 탐색
map_dirs = [d for d in os.listdir(base_dir) if os.path.isdir(os.path.join(base_dir, d)) and d.startswith('map')]

# 각 map 폴더 반복 처리
for map_num in map_dirs:
    print(f"Processing map: {map_num}")
    sim_dir = os.path.join(base_dir, map_num, 'gas_simulations')

    # 각 sim 폴더의 농도 계산 및 저장
    iterations = range(290, 311)  # 예시로 iteration 290부터 310까지 처리
    grid_shape = (104, 64, 25)  # 환경 그리드 사이즈 (필요에 맞게 조정 가능)
    gas_concentration_total = np.zeros(grid_shape)
    count = 0

    # 각 sim 폴더 처리
    for sim_index in range(1, 21):  # sim1부터 sim20까지 처리
        sim_num = f'sim{sim_index}'
        sim_subdir = os.path.join(sim_dir, sim_num)

        if os.path.exists(sim_subdir):
            print(f"Processing simulation: {sim_subdir}")

            for iteration in iterations:
                csv_path = os.path.join(sim_subdir, f'iteration_{iteration}.csv')

                if os.path.exists(csv_path):
                    # CSV 파일 로드 및 처리
                    column_names = pd.read_csv(csv_path, skiprows=2, nrows=1, header=None).values[0].tolist()
                    data = pd.read_csv(csv_path, skiprows=3, names=column_names)

                    # 필요한 데이터 추출 (필라멘트 위치, Sigma 값, Num Moles 값)
                    positions = data[['Position X', 'Position Y', 'Position Z']].values
                    sigma_values = data['Sigma'].values
                    num_moles = 100  # 예시로 num_moles 값을 설정, 메타데이터에서 직접 추출할 수 있음

                    # 환경 설정 (Grid 정의)
                    env_min = np.array([-0.2, -0.2, 0])
                    env_max = np.array([10.2, 6.2, 2.5])
                    num_cells = np.array([104, 64, 25])
                    x = np.linspace(env_min[0], env_max[0], num_cells[0])
                    y = np.linspace(env_min[1], env_max[1], num_cells[1])
                    z = np.linspace(env_min[2], env_max[2], num_cells[2])
                    grid_x, grid_y, grid_z = np.meshgrid(x, y, z, indexing='ij')

                    # 가스 농도 초기화 및 누적
                    gas_concentration = np.zeros(grid_shape)
                    for i in range(len(positions)):
                        filament_pos = positions[i]
                        sigma = sigma_values[i]
                        concentration = calculate_gas_concentration(filament_pos, sigma, num_moles, grid_x, grid_y, grid_z)
                        gas_concentration += concentration

                    # 누적 평균 계산용
                    gas_concentration_total += gas_concentration
                    count += 1

                    # 각 iteration마다 개별 concentration map 저장 (individual_maps 폴더)
                    individual_map_dir = os.path.join(base_dir, map_num, 'individual_maps', sim_num)
                    os.makedirs(individual_map_dir, exist_ok=True)
                    np.save(os.path.join(individual_map_dir, f'gas_concentration_map_{iteration}.npy'), gas_concentration)
                    print(f"Saved individual map for iteration {iteration}")

            # 평균 농도 지도 저장 (average_gas_concentration_map.npy)
            if count > 0:
                average_concentration_map = gas_concentration_total / count
                average_map_dir = os.path.join(base_dir, map_num)
                np.save(os.path.join(average_map_dir, 'average_gas_concentration_map.npy'), average_concentration_map)
                print(f"Saved average concentration map for {map_num}")

        else:
            print(f"Skipping non-existent directory {sim_subdir}")

In [1]:
import numpy as np
import pandas as pd
import os
import matplotlib.pyplot as plt

# 가스 농도 계산 함수 (Farrell’s Concentration Equation 적용)
def calculate_gas_concentration(filament_pos, sigma, num_moles, grid_x, grid_y, grid_z):
    distance = np.sqrt((grid_x - filament_pos[0]) ** 2 + (grid_y - filament_pos[1]) ** 2 + (grid_z - filament_pos[2]) ** 2)
    concentration = (num_moles / (np.sqrt(8 * np.pi**3) * sigma**3)) * np.exp(-distance**2 / (2 * sigma**2))
    return concentration

# 시각화 함수 정의 (필요한 경우)
def visualize_gas_concentration_2d_3d(grid_x, grid_y, grid_z, gas_concentration, slice_index, save_dir):
    # 2D 시각화
    plt.figure(figsize=(10, 6))
    levels = np.linspace(np.min(gas_concentration[:, :, slice_index]), 
                         np.max(gas_concentration[:, :, slice_index]), 300)
    contour = plt.contourf(grid_x[:, :, slice_index], grid_y[:, :, slice_index], 
                           gas_concentration[:, :, slice_index], levels=levels, cmap='viridis')
    plt.colorbar(contour)
    plt.title('Gas Concentration Map (2D)')
    plt.savefig(f'{save_dir}/gas_concentration_2d.png')  # 2D 이미지 저장
    plt.show()

    # 3D 시각화
    fig = plt.figure(figsize=(10, 8))
    ax = fig.add_subplot(111, projection='3d')
    ax.scatter(grid_x.flatten(), grid_y.flatten(), grid_z.flatten(), 
               c=gas_concentration.flatten(), cmap='viridis', marker='o')
    ax.set_xlabel('X Position (m)')
    ax.set_ylabel('Y Position (m)')
    ax.set_zlabel('Z Position (m)')
    plt.title('Gas Concentration Map (3D)')
    plt.savefig(f'{save_dir}/gas_concentration_3d.png')  # 3D 이미지 저장
    plt.show()

# 경로 설정
base_dir = '/home/piai/PABA/gaden/install/test_env/share/test_env/scenarios/2_suc_map/'

# 모든 map 폴더와 sim 폴더 탐색
map_dirs = [d for d in os.listdir(base_dir) if os.path.isdir(os.path.join(base_dir, d)) and d.startswith('map')]

# 각 map 폴더 반복 처리
for map_num in map_dirs:
    print(f"Processing map: {map_num}")
    sim_dir = os.path.join(base_dir, map_num, 'gas_simulations')

    # 각 sim 폴더의 농도 계산 및 저장
    iterations = range(290, 311)  # 예시로 iteration 290부터 310까지 처리
    grid_shape = (64, 64, 25)  # 환경 그리드 사이즈 (필요에 맞게 조정 가능)
    gas_concentration_total = np.zeros(grid_shape)
    count = 0

    # 각 sim 폴더 처리
    for sim_index in range(1, 21):  # sim1부터 sim20까지 처리
        sim_num = f'sim{sim_index}'
        sim_subdir = os.path.join(sim_dir, sim_num)

        if os.path.exists(sim_subdir):
            print(f"Processing simulation: {sim_subdir}")

            for iteration in iterations:
                csv_path = os.path.join(sim_subdir, f'iteration_{iteration}.csv')

                if os.path.exists(csv_path):
                    # CSV 파일 로드 및 처리
                    column_names = pd.read_csv(csv_path, skiprows=2, nrows=1, header=None).values[0].tolist()
                    data = pd.read_csv(csv_path, skiprows=3, names=column_names)

                    # 필요한 데이터 추출 (필라멘트 위치, Sigma 값, Num Moles 값)
                    positions = data[['Position X', 'Position Y', 'Position Z']].values
                    sigma_values = data['Sigma'].values
                    num_moles = 100  # 예시로 num_moles 값을 설정, 메타데이터에서 직접 추출할 수 있음

                    # 환경 설정 (Grid 정의)
                    env_min = np.array([-0.2, -0.2, 0])
                    env_max = np.array([10.2, 6.2, 2.5])
                    num_cells = np.array([64, 64, 25]) 
                    x = np.linspace(env_min[0], env_max[0], num_cells[0])
                    y = np.linspace(env_min[1], env_max[1], num_cells[1])
                    z = np.linspace(env_min[2], env_max[2], num_cells[2])
                    grid_x, grid_y, grid_z = np.meshgrid(x, y, z, indexing='ij')
                    grid_shape = grid_x.shape

                    # 가스 농도 초기화 및 누적
                    gas_concentration = np.zeros(grid_shape)
                    for i in range(len(positions)):
                        filament_pos = positions[i]
                        sigma = sigma_values[i]
                        concentration = calculate_gas_concentration(filament_pos, sigma, num_moles, grid_x, grid_y, grid_z)
                        gas_concentration += concentration

                    # 누적 평균 계산용
                    gas_concentration_total += gas_concentration
                    count += 1

                    # 각 iteration마다 개별 concentration map 저장 (각 map 폴더 내 individual_maps 폴더)
                    individual_map_dir = os.path.join(base_dir, map_num, 'individual_maps', sim_num)
                    os.makedirs(individual_map_dir, exist_ok=True)
                    np.save(os.path.join(individual_map_dir, f'gas_concentration_map_{iteration}.npy'), gas_concentration)
                    print(f"Saved individual map for iteration {iteration} in {individual_map_dir}")

            # 평균 농도 지도 저장 (각 map 폴더 내 average_gas_concentration_map.npy)
            if count > 0:
                average_concentration_map = gas_concentration_total / count
                average_map_dir = os.path.join(base_dir, map_num)
                np.save(os.path.join(average_map_dir, 'average_gas_concentration_map.npy'), average_concentration_map)
                print(f"Saved average concentration map for {map_num} in {average_map_dir}")

        else:
            print(f"Skipping non-existent directory {sim_subdir}")

Processing map: map93
Processing simulation: /home/piai/PABA/gaden/install/test_env/share/test_env/scenarios/2_suc_map/map93/gas_simulations/sim1
Saved individual map for iteration 290 in /home/piai/PABA/gaden/install/test_env/share/test_env/scenarios/2_suc_map/map93/individual_maps/sim1
Saved individual map for iteration 291 in /home/piai/PABA/gaden/install/test_env/share/test_env/scenarios/2_suc_map/map93/individual_maps/sim1
Saved individual map for iteration 292 in /home/piai/PABA/gaden/install/test_env/share/test_env/scenarios/2_suc_map/map93/individual_maps/sim1
Saved individual map for iteration 293 in /home/piai/PABA/gaden/install/test_env/share/test_env/scenarios/2_suc_map/map93/individual_maps/sim1
Saved individual map for iteration 294 in /home/piai/PABA/gaden/install/test_env/share/test_env/scenarios/2_suc_map/map93/individual_maps/sim1
Saved individual map for iteration 295 in /home/piai/PABA/gaden/install/test_env/share/test_env/scenarios/2_suc_map/map93/individual_maps/s